# NLP-LAB Exercise 01 by jonas weinz
----

In [1]:
%matplotlib ipympl
import nltk
import pprint
from sklearn.tree import DecisionTreeClassifier
from sklearn.feature_extraction import DictVectorizer
from sklearn.pipeline import Pipeline

## implementing own classifiers

* writing an own feature funtion

In [2]:
def features(sentence, index):
    word = sentence[index]
    is_punctuation_mark = word == "!" or word == "." or word == "," or word == "?"
    sentence_length = len(sentence)
    relative_third = (index * 3) // sentence_length 
    vowels = word.count('a') + word.count('e') + word.count('i') + word.count('o') + word.count('u')
    return {
        'word': word,
        'is_capitalized': sentence[index][0].upper() == sentence[index][0],
        'prefix-1': sentence[index][0],
        'suffix-1': sentence[index][-1],
        'prefix-2': sentence[index][1] if len(word) > 1 else '',
        'suffix-2': sentence[index][-2] if len(word) > 1 else '',
        'prev_word': '' if index == 0 else sentence[index - 1],
        'next_word': '' if index == len(sentence) - 1 else sentence[index + 1],
        'length': len(word),
        'index' : index,
        'rev_index': len(sentence) - index,
        'sentence_length_': len(sentence),
        'relative_third': relative_third,
        'numerical': word.isnumeric(),
        'is_punctuation_mark': is_punctuation_mark,
        ',': word == ",",
        '.': word == ".",
        '!': word == "!",
        '?': word == "?",
        'vowels' : vowels
    }
'''
    return {
        'word': word,
        'is_capitalized': word[0].upper() == word[0],
        'prefix-1': word[0],
        'suffix-1': word[-1],
        'prev_word': '' if index == 0 else sentence[index - 1],
        'next_word': '' if index == len(sentence) - 1 else sentence[index + 1],
        'length': len(word),
        'index' : index,
        'rev_index': len(sentence) - index,
        'sentence_length': len(sentence)#,
        'relative_third': relative_third,
        'is_punctuation_mark': is_punctuation_mark,
        ',': word == ",",
        '.': word == ".",
        '!': word == "!",
        '?': word == "?"
    }
'''

'\n    return {\n        \'word\': word,\n        \'is_capitalized\': word[0].upper() == word[0],\n        \'prefix-1\': word[0],\n        \'suffix-1\': word[-1],\n        \'prev_word\': \'\' if index == 0 else sentence[index - 1],\n        \'next_word\': \'\' if index == len(sentence) - 1 else sentence[index + 1],\n        \'length\': len(word),\n        \'index\' : index,\n        \'rev_index\': len(sentence) - index,\n        \'sentence_length\': len(sentence)#,\n        \'relative_third\': relative_third,\n        \'is_punctuation_mark\': is_punctuation_mark,\n        \',\': word == ",",\n        \'.\': word == ".",\n        \'!\': word == "!",\n        \'?\': word == "?"\n    }\n'

In [3]:
test_sentence = ['The','cake','is','a','lie','!']
#for i in range(len(test_sentence)):
#    pprint.pprint(features(test_sentence, i))

* function for creating training sets

In [4]:
def untag(tagged_sentence):
    return [w for w,t in tagged_sentence]

def transform_to_dataset(tagged_sentences):
    X,y = [], []
    
    for s in tagged_sentences:
        for i in range(len(s)):
            X.append(features(untag(s),i))
            y.append(s[i][1])
    return X,y

def create_training_and_test_set(annotated_sentences, relative_cutoff):
    cutoff = int(relative_cutoff * len(annotated_sentences))
    training_sentences = annotated_sentences[:cutoff]
    test_sentences = annotated_sentences[cutoff:]
    
    X,y = transform_to_dataset(training_sentences)
    tX, ty = transform_to_dataset(test_sentences)
    
    return X,y,tX,ty

* Decision Tree classifier

In [5]:
def train_classifier(X,y,classifier,max_size=10000):
    clf = Pipeline([
        ('vectorizer', DictVectorizer(sparse=False)),
        ('classifier', classifier)
    ])
    
    print("start training…")
    
    clf.fit(
        X if len(X) < max_size else X[:max_size],
        y if len(y) < max_size else y[:max_size]
    )
    
    print("training done")
    
    return clf

* classifier evaluater

In [6]:
def test_classifier(clf, tX, ty):
    accuracy = clf.score(tX, ty)
    print("Accuracy: ", accuracy)
    # TODO: more analytics
    return accuracy

## Exercise 01:

### Performance 1


#### Model 01
* train and testing english custom POS tagger model:

In [7]:
def model_01(X,y,tX,ty, max_size=1000):
    #classifier = DecisionTreeClassifier(criterion='entropy')
    from sklearn.neural_network import MLPClassifier
    model01_clf = train_classifier(X,y,MLPClassifier(),max_size=1000)
    return test_classifier(clf=model01_clf, tX=tX, ty=ty)

#### Model 02

In [8]:
def model_02(tX,ty):
    m2_y = nltk.pos_tag([w['word'] for w in tX])
    # compare results
    n_correct = sum((1 if m2_y[i][1] == ty[i] else 0) for i in range(len(ty)))
    return n_correct / len(ty)

#### Model 03

In [9]:
def model_03(corpus_tagged, corpus_sents, cut=0.8):
    
    patterns = [(r'.*ing$', 'VBG'), (r'.*ed$', 'VBD'), (r'.*es$', 'VBZ'), (r'.*ould$', 'MD'), (r'.*\'s$', 'NN$'),               
             (r'.*s$', 'NNS'), (r'^-?[0-9]+(.[0-9]+)?$', 'CD'), (r'.*', 'NN')]
    
    s = int(len(corpus_tagged) * cut)
    train_sents = corpus_tagged[:s]
    test_sents = corpus_tagged[s:]
    
    models = {
        'def_model': nltk.DefaultTagger('NN'),
        'regexp_model': nltk.RegexpTagger(patterns),
        'uni_model': nltk.UnigramTagger(train_sents),
        'bi_model': nltk.BigramTagger(train_sents),
        'tri_model': nltk.TrigramTagger(train_sents)
    }
    
    performance = {}
    for name,model in models.items():
        performance[name] = model.evaluate(test_sents)
    
    return performance


### Applying models on Datasets

In [10]:
performances = {}

treebank_tagged = nltk.corpus.treebank.tagged_sents()
treebank_sents = nltk.corpus.treebank.sents()

brown_tagged = nltk.corpus.brown.tagged_sents()#(categories='news')
brown_sents = nltk.corpus.brown.sents()#(categories='news')

X1,y1,tX1,ty1 = create_training_and_test_set(annotated_sentences=treebank_tagged, 
                                         relative_cutoff=0.8)

X2,y2,tX2,ty2 = create_training_and_test_set(annotated_sentences=brown_tagged, 
                                         relative_cutoff=0.8)


print("P1.1")
performances['P1.1'] = model_01(X1,y1,tX1,ty1)

print("P1.2")
performances['P1.2'] = model_02(tX1,ty1)

print("P1.3")
p3 = model_03(treebank_tagged, treebank_sents)
for k,v in p3.items():
    performances["P1.3 -- " + k] = v

print("P1.4")
performances['P1.4'] = model_01(X2,y2,tX2,ty2)

print("P1.5")
performances['P1.5'] = model_02(tX2,ty2)

print("P1.6")
p6 = model_03(brown_tagged, brown_sents)
for k,v in p3.items():
    performances["P1.6 -- " + k] = v

pprint.pprint(performances)


P1.1
start training…
training done
Accuracy:  0.7712959728529368
P1.2
P1.3
P1.4
start training…
training done
Accuracy:  0.6410882090489463
P1.5
P1.6
{'P1.1': 0.7712959728529368,
 'P1.2': 0.8936074654423873,
 'P1.3 -- bi_model': 0.1132791057437996,
 'P1.3 -- def_model': 0.1447677029791906,
 'P1.3 -- regexp_model': 0.24232746145017217,
 'P1.3 -- tri_model': 0.06736863116922003,
 'P1.3 -- uni_model': 0.8608213982733669,
 'P1.4': 0.6410882090489463,
 'P1.5': 0.6044583741861567,
 'P1.6 -- bi_model': 0.1132791057437996,
 'P1.6 -- def_model': 0.1447677029791906,
 'P1.6 -- regexp_model': 0.24232746145017217,
 'P1.6 -- tri_model': 0.06736863116922003,
 'P1.6 -- uni_model': 0.8608213982733669}


### Plotting Data

In [11]:
import matplotlib.pyplot as plt
import numpy as np
#weights = clf.named_steps['classifier'].feature_importances_
#labels = clf.named_steps['vectorizer'].get_feature_names()

#sort
#weights, labels = (list(t) for t in zip(*sorted(zip(weights, labels))))

fig_1, ax_1 = plt.subplots()
plt.bar(np.arange(len(performances)), performances.values())
plt.xticks(np.arange(len(performances)), performances.keys(), rotation=30, ha='right')
plt.tight_layout()
plt.show()


FigureCanvasNbAgg()